In [115]:
import pandas as pd
import numpy as np
import requests
import altair as alt
import matplotlib.pyplot as plt

In [116]:
def get_data(year, url):
    key = "Bearer PNkaVR4Ti/Mr9d+LMxa875mI9Yvl5fw8EvZRuJDWnC6KN+1O1Cl3g5tB/YLq8hix"
    header = {'Authorization':key}
    params = {'year':year}


    response = requests.get(f"http://api.collegefootballdata.com/{url}",
                            headers=header,
                            params=params)

    response_json = response.json()

    recruiting = pd.json_normalize(response_json)
    
    return recruiting

In [117]:
BEGIN_YEAR = 2015
END_YEAR = 2021

In [118]:
# IRS income dataset
income = pd.concat([pd.read_csv(f"{year}zpallagi.csv") for year in (15, 16, 17, 19, 20)])

# Coordinates with zip codes
zips_coordinates = pd.read_csv("zip_code_database.csv")
zips_coordinates_og = zips_coordinates.copy()
# replace 
cfb = pd.concat([get_data(year, "recruiting/players") for year in range(BEGIN_YEAR, END_YEAR + 2, 1)])

In [119]:
# data for win%
cfb_results = pd.concat([get_data(year, "records") for year in range(BEGIN_YEAR, END_YEAR + 2)])

In [120]:
position_dict = {
    'RET' : "returner",
    "FB" : "full back",
    "LS" : "long snapper",
    "EDGE" : "edge",
    "QB" : "quarterback",
    "IOL" : "interior offensive line",
    "P" : "punter",
    "LB" : "linebacker",
    "DL" : "defensive lineman",
    "K" : "kicker",
    "APB" : "all purpose back",
    "OC" : "center",
    "DUAL" : "quarterback",
    "PRO" : "quarterback",
    "WDE" : "weak side defensive end",
    "ILB" : "inside linebacker",
    "SDE" : "strong side defensive end", 
    "TE" : "tight end",
    "OG" : "offensive guard",
    "DT" : "defensive tackle",
    "OLB" : "outside linebacker",
    "RB" : "running back",
    "S" : "safety",
    "ATH" : "athlete",
    "OT" : "offensive tackle",
    "CB" : "cornerback",
    "WR" : "wide receiver"
}

In [121]:
special_teams = ['RET', 'LS', 'P', 'K']
defensive_line = ['EDGE', 'DL', 'WDE', 'SDE', 'DT']
linebackers = ["LB", "ILB", "OLB"]
secondary = ["CB", "S"]
backs = ['FB', "APB", "RB"]
receivers = ["WR", "TE"]
offensive_line = ["IOL", "OC", "OG", "OT"]
other = ["ATH"]
qb = ['QB', 'DUAL', 'PRO']

In [122]:
def assign_position_group(position):
    if position in special_teams:
        return "special teams"
    
    elif position in defensive_line:
        return "defensive line"
    
    elif position in linebackers:
        return "linebackers"
    
    elif position in secondary:
        return "secondary"
    
    elif position in backs:
        return "backs"
    
    elif position in receivers:
        return "receiver"
    
    elif position in offensive_line:
        return "offensive line"
    
    elif position in qb:
        return "quarterback"
    
    else:
        return "other"

In [123]:
cfb['position'] = cfb['position'].apply(lambda x: assign_position_group(x))

In [124]:
# removing schools with little representation
cfb = cfb[cfb['committedTo'].isin(cfb.groupby("committedTo").size().sort_values().head(100).index) == False]

In [125]:
# isolating and removing non-US recruits
non_us_players = [cfb['hometownInfo.latitude'].isna()]
cfb = cfb[cfb['hometownInfo.latitude'].isna() == False]

In [126]:
# slimming down dfs for visual ease
relevant_columns_income = ['STATE', 'zipcode', 'A02650']

relevant_columns_linking_info = ['state', 'zip', 'primary_city', 'latitude', 'longitude']

income = income[relevant_columns_income]

zips_coordinates = zips_coordinates[relevant_columns_linking_info]

In [127]:
# coordinates with zip
zips_coordinates.head()

state  zip primary_city  latitude  longitude
0    NY  501   Holtsville     40.81     -73.04
1    NY  544   Holtsville     40.81     -73.04
2    PR  601     Adjuntas     18.16     -66.72
3    PR  602       Aguada     18.38     -67.18
4    PR  603    Aguadilla     18.43     -67.15

In [128]:
# income info
income.head()

STATE  zipcode      A02650
0    AL        0  11036309.0
1    AL        0  17960153.0
2    AL        0  16216787.0
3    AL        0  14588959.0
4    AL        0  28985528.0

In [129]:
# avg income by zipcode
median_income_by_zipcode = income.merge(zips_coordinates, left_on=['zipcode'], right_on=['zip']).groupby("zipcode").A02650.median().reset_index()


In [130]:
# avg income by zipcode
median_income_by_zipcode = income.merge(zips_coordinates, left_on=['zipcode'], right_on=['zip']).groupby("zipcode").A02650.median().reset_index()


In [131]:
# merging with other info
merged_income_zipcor = zips_coordinates.merge(median_income_by_zipcode, left_on=['zip'], right_on=['zipcode'])

In [132]:
# adjusting coordinates for merging
merged_income_zipcor['adj_lat'] = merged_income_zipcor['latitude'].apply(lambda x: float(str(x).split(".")[0]))
merged_income_zipcor['adj_lng'] = merged_income_zipcor['longitude'].apply(lambda x: float(str(x).split(".")[0]))

In [133]:
# adjusting coordinates for merging
zips_coordinates_og['adj_lat'] = zips_coordinates_og['latitude'].apply(lambda x: float(str(x).split(".")[0]))
zips_coordinates_og['adj_lng'] = zips_coordinates_og['longitude'].apply(lambda x: float(str(x).split(".")[0]))

In [134]:
# adjusting coordinates for merging
cfb['lat_adj'] = cfb['hometownInfo.latitude'].apply(lambda x: float(str(x).split(".")[0]))
cfb['lng_adj'] = cfb['hometownInfo.longitude'].apply(lambda x: float(str(x).split(".")[0]))

In [135]:
# getting average income by city
income_by_city_state_coord = merged_income_zipcor.groupby(['primary_city', 'state', 'adj_lat', 'adj_lng']).A02650.median().reset_index()
income_by_city_state_coord['A02650'] = income_by_city_state_coord['A02650'].round()
income_by_city_state_coord = income_by_city_state_coord.rename(columns={"A02650" : "average_income"})


In [136]:
# getting average income by city **** FOR DISPLAYING DIFFERENCE IN USING ADJ COORD AND NOT *****
income_by_city_state_coord_ = merged_income_zipcor.groupby(['primary_city', 'state']).A02650.median().reset_index()
income_by_city_state_coord_['A02650'] = income_by_city_state_coord_['A02650'].round()
income_by_city_state_coord_ = income_by_city_state_coord_.rename(columns={"A02650" : "average_income"})


# Aside: why we use adj coordinates

## We use adj lat and adj long for greater specificity when split - apply - comibing data, as well as merging the data 

### not using adj lat and long: 

In [137]:
income_by_city_state_coord_[(income_by_city_state_coord_['primary_city'] == 'Saint Paul')
                            &
                            (income_by_city_state_coord_['state'] == 'MN')]

primary_city state  average_income
19720   Saint Paul    MN        116110.0

### using adj lat and long:  

In [138]:
income_by_city_state_coord[(income_by_city_state_coord['primary_city'] == 'Saint Paul') 
                           &
                           (income_by_city_state_coord['state'] == 'MN')]

primary_city state  adj_lat  adj_lng  average_income
19907   Saint Paul    MN     44.0    -93.0        109955.0
19908   Saint Paul    MN     44.0    -92.0        152032.0
19909   Saint Paul    MN     45.0    -93.0        165376.0
19910   Saint Paul    MN     45.0    -92.0         33470.0

## Another advantage of using adj coordinates is preventing issues that arise when there are multiple cities with the same name in the same state - did not find that to be a problem in our data

# Back to data creation...

In [140]:
# joining together for final df
final = cfb.merge(income_by_city_state_coord, left_on=['city', 'stateProvince', 'lat_adj', 'lng_adj'],
                                       right_on=['primary_city', 'state', 'adj_lat', 'adj_lng'])

In [141]:
# handling duplicates
final = final.groupby(['name', 'committedTo']).first().reset_index()

In [142]:
# removing unranked
final = final[final['ranking'].isna() == False]

In [143]:
# removing those with missing info
final = final[(final['height'].isna() == False) & (final['weight'].isna() == False)]

In [144]:
# final dupe check
final = final[final[['name', 'hometownInfo.longitude']].duplicated() == False]

In [145]:
# new column for overall ranking across all years for players
final['entire_dataset_ranking'] = final['rating'].rank(ascending=False)

# Linking with team results

In [146]:
cfb_results['win%'] = cfb_results['total.wins'] / cfb_results['total.games']

In [183]:
final_with_results = final.merge(cfb_results[['team', 'year', 'conference', 'division', 'win%']],
            left_on=['committedTo', 'year'], right_on=['team', 'year'], how='left')

In [184]:
final_with_results = final_with_results[final_with_results['win%'].isna() == False]

In [185]:
# agg correlation results
final_with_results.groupby("team")[['win%', "rating", 'average_income', 'stars']].mean().corr()

win%    rating  average_income     stars
win%            1.000000  0.523666       -0.100526  0.531315
rating          0.523666  1.000000        0.016041  0.994045
average_income -0.100526  0.016041        1.000000  0.021688
stars           0.531315  0.994045        0.021688  1.000000

In [201]:
outcome_corr_by_position = final_with_results[['position', 'win%', 'rating', 'average_income', 'stars']].groupby("position").corr().reset_index()


In [204]:
qbs_and_dline = outcome_corr_by_position[outcome_corr_by_position['position'].isin(['quarterback', 'defensive line'])]

In [212]:
# correlation for positions
outcome_corr_by_position[outcome_corr_by_position['level_1'] == 'stars'].sort_values(by='win%')

position level_1      win%    rating  average_income  stars
19           other   stars  0.154488  0.871224       -0.049544    1.0
35   special teams   stars  0.164432  0.838422       -0.031678    1.0
23     quarterback   stars  0.203974  0.893500        0.106268    1.0
27        receiver   stars  0.228570  0.891601        0.040701    1.0
3            backs   stars  0.229302  0.899445        0.011183    1.0
11     linebackers   stars  0.229774  0.896239        0.000659    1.0
31       secondary   stars  0.244313  0.895264        0.028547    1.0
7   defensive line   stars  0.258175  0.903631       -0.004169    1.0
15  offensive line   stars  0.261892  0.894140        0.026101    1.0

In [207]:
qbs_and_dline.set_index(["position", "level_1"])

win%    rating  average_income     stars
position       level_1                                                     
defensive line win%            1.000000  0.299831       -0.025569  0.258175
               rating          0.299831  1.000000       -0.002208  0.903631
               average_income -0.025569 -0.002208        1.000000 -0.004169
               stars           0.258175  0.903631       -0.004169  1.000000
quarterback    win%            1.000000  0.222576       -0.015491  0.203974
               rating          0.222576  1.000000        0.099844  0.893500
               average_income -0.015491  0.099844        1.000000  0.106268
               stars           0.203974  0.893500        0.106268  1.000000

In [151]:
plot_this = final_with_results.groupby(['team', "year"])[['win%', 'rating', 'average_income']].mean().reset_index()

In [155]:
teams = list(plot_this.groupby("team")['rating'].median().sort_values(ascending=False).index)

In [159]:
input_dropdown = alt.binding_select(options=teams, name='team')


selection = alt.selection_single(fields=['team'], bind=input_dropdown)


color = alt.condition(selection,
                    alt.Color('year:N'),
                    alt.value('lightgray'))



alt.Chart(plot_this).mark_circle(size=100)\
.encode(x=alt.X('average_income',
        scale=alt.Scale(domain=[plot_this['average_income'].min(), 
                                plot_this['average_income'].max()])), 
        y=alt.Y('win%',
        scale=alt.Scale(domain=[plot_this['win%'].min(), 
                                plot_this['win%'].max()])),
        color=color)\
.add_selection(
    selection)

alt.Chart(...)

# Interactive visuals

In [160]:
plt_sample = final_with_results.sample(5000)

In [161]:
plt_sample['rounded_rating'] = plt_sample['rating'].round(2)

In [162]:
teams = list(plt_sample.groupby("committedTo")['rating'].median().sort_values(ascending=False).index)

In [163]:
input_dropdown = alt.binding_select(options=teams, name='school')


selection = alt.selection_single(fields=['committedTo'], bind=input_dropdown)


color = alt.condition(selection,
                    'stars',
                    alt.value('lightgray'))


In [164]:

alt.Chart(plt_sample).mark_circle(size=60)\
.encode(x=alt.X('rating',
        scale=alt.Scale(domain=[plt_sample['rating'].min(), 
                                plt_sample['rating'].max()])), 
        y='win%',
        color=color)\
.add_selection(
    selection)

alt.Chart(...)

In [165]:
input_dropdown = alt.binding_select(options=list(set(plt_sample['committedTo'])), name='comittedTo')
selection = alt.selection_single(fields=['committedTo'], bind=input_dropdown)

alt.Chart(plt_sample).mark_bar().encode(
    alt.X("rounded_rating:Q", bin=alt.BinParams()),
    y='count(*):Q'
).add_selection(
    selection
).transform_filter(
    selection
)

alt.Chart(...)

# Making rankings team level table

In [166]:
avg_rating_by_team = final.groupby("committedTo").rating.median().sort_values().reset_index()

In [167]:
avg_income_by_team = final.groupby("committedTo").average_income.median().reset_index()

In [168]:
team_rating_and_ranking = pd.merge(avg_rating_by_team, avg_income_by_team)

In [169]:
team_rating_and_ranking['talent_ranking'] = team_rating_and_ranking['rating'].rank(ascending=False)

In [170]:
team_rating_and_ranking['income_ranking'] = team_rating_and_ranking['average_income'].rank(ascending=False)

In [171]:
team_rating_and_ranking[['committedTo', 'talent_ranking', 'income_ranking']]

committedTo  talent_ranking  income_ranking
0        Kennesaw State           172.0           156.0
1           Austin Peay           170.5           129.5
2          North Dakota           170.5            82.0
3                Furman           169.0            70.5
4    Grand Valley State           166.0            37.0
..                  ...             ...             ...
167             Clemson             5.0           117.5
168                 LSU             4.0           159.0
169          Ohio State             3.0           107.0
170             Georgia             2.0            76.0
171             Alabama             1.0           136.0

[172 rows x 3 columns]

# Regression

In [172]:
from sklearn.linear_model import LinearRegression

In [173]:
state_dummies = pd.get_dummies(final['state']).drop("MI", axis=1)

In [174]:
X = pd.concat((final[['average_income',
                      'height', 'weight']], state_dummies), axis=1)

In [231]:
y = final['entire_dataset_ranking'] 

In [232]:
lr = LinearRegression().fit(X, y)

In [233]:
df = pd.DataFrame()
df['coefficients'] = np.round(lr.coef_.tolist()[0], 6)
df['feature_names'] = lr.feature_names_in_.tolist()

In [234]:
from statsmodels.api import OLS

In [235]:
import numpy as np

import statsmodels.api as sm

In [236]:

## fit a OLS model with intercept on TV and Radio 
X = sm.add_constant(X) 
est = sm.OLS(y, X).fit() 
est.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                              OLS Regression Results                              
==================================================================================
Dep. Variable:     entire_dataset_ranking   R-squared:                       0.041
Model:                                OLS   Adj. R-squared:                  0.038
Method:                     Least Squares   F-statistic:                     17.37
Date:                    Fri, 10 Feb 2023   Prob (F-statistic):          4.66e-152
Time:                            15:23:35   Log-Likelihood:            -2.1659e+05
No. Observations:                   21389   AIC:                         4.333e+05
Df Residuals:                       21336   BIC:                         4.337e+05
Df Model:                              52                                         
Covariance Type:                nonrobust                                         
==================================================================================
                     coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------
const           3.495e+04   1494.665     23.381      0.000     3.2e+04    3.79e+04
average_income    -0.0019      0.001     -2.877      0.004      -0.003      -0.001
height          -313.9948     21.949    -14.306      0.000    -357.017    -270.973
weight             0.1159      1.233      0.094      0.925      -2.301       2.533
AK              1806.4883   6061.703      0.298      0.766   -1.01e+04    1.37e+04
AL              -739.6070    327.558     -2.258      0.024   -1381.645     -97.569
AR              -570.5221    490.929     -1.162      0.245   -1532.779     391.735
AZ               379.7906    390.623      0.972      0.331    -385.861    1145.442
CA             -1132.8210    283.949     -3.990      0.000   -1689.382    -576.260
CO               922.0582    510.574      1.806      0.071     -78.704    1922.821
CT              -717.4865    624.939     -1.148      0.251   -1942.413     507.440
DC             -3411.7640    620.270     -5.500      0.000   -4627.539   -2195.989
DE              1093.3669   1260.594      0.867      0.386   -1377.492    3564.225
FL             -1889.0123    272.369     -6.935      0.000   -2422.876   -1355.148
GA             -1562.5241    284.632     -5.490      0.000   -2120.423   -1004.625
HI              -574.6001    528.698     -1.087      0.277   -1610.888     461.688
IA              -543.3006    550.825     -0.986      0.324   -1622.959     536.357
ID              3367.5687    860.157      3.915      0.000    1681.596    5053.542
IL               279.6731    352.298      0.794      0.427    -410.858     970.204
IN               417.1137    409.069      1.020      0.308    -384.691    1218.919
KS             -1169.0538    590.801     -1.979      0.048   -2327.068     -11.040
KY               703.9835    485.430      1.450      0.147    -247.496    1655.463
LA             -2305.7881    334.097     -6.902      0.000   -2960.642   -1650.934
MA               871.0225    596.750      1.460      0.144    -298.652    2040.697
MD             -2135.7453    391.145     -5.460      0.000   -2902.419   -1369.072
ME              1190.1170   3038.197      0.392      0.695   -4764.978    7145.212
MN              3492.0530    492.805      7.086      0.000    2526.118    4457.988
MO             -1564.6760    437.682     -3.575      0.000   -2422.565    -706.787
MS             -2269.9860    393.890     -5.763      0.000   -3042.039   -1497.932
MT              5781.5535   2301.946      2.512      0.012    1269.566    1.03e+04
NC             -1099.5200    336.151     -3.271      0.001   -1758.401    -440.639
ND              4679.0590   1930.861      2.423      0.015     894.425    8463.693
NE               238.4618    705.130      0.338      0.735   -1143.645    1620.569
NH                36.8854   2484.782      0.015    